# Taxi Driver Program
Reinforcement Learning algorithm that solves the Taxi-v3 environment from OpenAI gym library

### Two possible modes:
1. User mode: Input parameters to play with optimization
2. Time mode: Input time for algorithm to find a solution

## Functionality
Run all cells, and then go to Program Frontend heading to run desired game mode.
Each mode contains instructions in documentation string

## Training

In [1]:
import gym
import numpy as np
import random
import pandas as pd
import torch
import plotly.express as px

In [2]:
env = gym.make('Taxi-v3')
env.reset()
env.render()
action_size = env.action_space.n
state_size = env.observation_space.n

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+



In [3]:
# DEFAULT PARAMS
TOTAL_TEST_EP = 100
TOTAL_EP = 1500
MAX_STEPS = 1000
LR = 0.97
GAMMA = 0.95
EPSILON = 0.95
MAX_EPSILON = 1.0
MIN_EPSILON = 0.01
DECAY_RATE = 0.01
Q_TABLE = np.zeros((state_size, action_size))
OPTIMIZED = False


In [4]:
def calculate_q_table(
    total_ep = TOTAL_EP,
    max_steps = MAX_STEPS,
    lr = LR,
    gamma = GAMMA,
    epsilon = EPSILON,
    max_epsilon = MAX_EPSILON,
    min_epsilon = MIN_EPSILON,
    decay_rate = DECAY_RATE,
    q_table = Q_TABLE
):
    '''
    Run training on taxi env to calculate Q-table
    :param total_ep: total episodes to be run
    :param max_steps: maximum amount steps per episode
    :param lr: learning rate of q-function
    :param gamma: discount factor for q-function
    :param epsilon: initial epsilon value
    :param max_epsilon: max epsilon for epsilon calculation
    :param min_epsilon: min epsilon for epsilon calculation
    :param decay_rate: exploration decay rate for q-function
    :return:
    '''
    train_rewards_per_ep_total = []
    train_penalties_per_ep_total = []
    train_timestep_per_ep_total = []
    train_max_cost_per_ep_total = []

    for episode in range(total_ep):

        # Reset Environment:
        state = env.reset()
        step = 0
        done = False

        total_penalties_in_episode = 0
        total_rewards_in_episode = 0
        total_max_cost_in_episode = 0

        for step in range(max_steps):

            # Choose an action a in the current world state(s) (step 3)
            # First we randomize a number
            exp_exp_tradeoff = random.uniform(0, 1)

            # If this number > greater than epsilon --> exploitation (taking the biggest q value for the current state):
            if exp_exp_tradeoff > epsilon:
                action = np.argmax(q_table[state, :])

            # Else, doing random choice:
            else:
                action = env.action_space.sample()

            # Take the action (a) and observe the outcome state (s') and the reward (r)
            new_state, reward, done, info = env.step(action)

            if reward == -10:
                total_penalties_in_episode += 1

            if reward < total_max_cost_in_episode:
                total_max_cost_in_episode = reward


            total_rewards_in_episode += reward

            # Update Q(s,a):= Q(s,a) + lr [R(s,a) + gamma * max Q(s',a') - Q(s,a)]
            q_table[state, action] = q_table[state, action] + lr * (reward + gamma *
                                            np.max(q_table[new_state, :]) - q_table[state, action])

            # Our new state:
            state = new_state

            # If done True, finish the episode:
            if done:
                train_rewards_per_ep_total.append(total_rewards_in_episode)
                train_penalties_per_ep_total.append(total_penalties_in_episode)
                train_timestep_per_ep_total.append(step)
                train_max_cost_per_ep_total.append(total_max_cost_in_episode)
                break

        # Increment number of episodes:
        episode += 1

        # Reduce epsilon (because we need less and less exploration):
        epsilon = min_epsilon + (max_epsilon - min_epsilon) *np.exp(-decay_rate*episode)
    return q_table, train_rewards_per_ep_total, train_timestep_per_ep_total, train_penalties_per_ep_total, train_max_cost_per_ep_total

## Optimization

In [5]:
def gridsearch(lr_range, gamma_range, epsilon_range):
    '''
    Run a gridsearch on Q-Learning to output best combination
    :param lr_range: range to test learning rate
    :param gamma_range: range to test gamma
    :param epsilon_range: range to test epsilon
    :return: DataFrame of rewards, timesteps, penalties and cost, per episode
    '''
    results = pd.DataFrame()

    for lr in lr_range:
        for gamma in gamma_range:
            for epsilon in epsilon_range:
                q_table, rewards, timestep, penalties, cost = calculate_q_table(
                    lr=lr,
                    gamma=gamma,
                    epsilon=epsilon
                )
                results_ = pd.DataFrame({
                    'learning_rate':  float(lr),
                    'gamma':  float(gamma),
                    'epsilon':  float(epsilon),
                    'rewards': rewards,
                    'timesteps':  timestep,
                    'penalties':  penalties,
                    'cost':  cost,
                })
                
                results = results.append(results_)

    # index -> episode
    results = results.reset_index().rename(columns={'index': 'episode'})

    # add column with the 2 hyper-parameters
    results['hyperparameters'] = [f'lr={l}, gamma={g}, epsilon={e}' for (l, g, e) in zip(results['learning_rate'], results['gamma'], results['epsilon'])]

    print(results.head())


    return results

In [6]:
optimized_data = gridsearch(
    lr_range=np.linspace(0.95,1.0, num=3),
    gamma_range=np.linspace(0.95,1.0, num=3),
    epsilon_range=np.linspace(0.95,1.0, num=3)
)

# Plot superimposed gridsearch curves per episode
fig = px.line(optimized_data, x='episode', y='timesteps', color='hyperparameters')
fig.show()
fig = px.line(optimized_data, x='episode', y='rewards', color='hyperparameters')
fig.show()
fig = px.line(optimized_data, x='episode', y='penalties', color='hyperparameters')
fig.show()
fig = px.line(optimized_data, x='episode', y='cost', color='hyperparameters')
fig.show()

/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_21710/2363394178.py:29: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(results_)
/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_21710/2363394178.py:29: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(results_)
/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_21710/2363394178.py:29: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append(results_)
/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_21710/2363394178.py:29: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.appen

   episode  learning_rate  gamma  epsilon  rewards  timesteps  penalties  \
0        0           0.95   0.95     0.95     -731        199         59   
1        1           0.95   0.95     0.95     -812        199         68   
2        2           0.95   0.95     0.95     -704        199         56   
3        3           0.95   0.95     0.95     -713        199         57   
4        4           0.95   0.95     0.95     -767        199         63   

   cost                    hyperparameters  
0   -10  lr=0.95, gamma=0.95, epsilon=0.95  
1   -10  lr=0.95, gamma=0.95, epsilon=0.95  
2   -10  lr=0.95, gamma=0.95, epsilon=0.95  
3   -10  lr=0.95, gamma=0.95, epsilon=0.95  
4   -10  lr=0.95, gamma=0.95, epsilon=0.95  


## Inference

In [7]:
def run_taxi_driver_with_calculated_q_table(
        total_test_ep=TOTAL_TEST_EP,
        max_steps=MAX_STEPS,
        q_table=Q_TABLE
):
    '''
    Run the taxi game with the existing q-table
    :param total_test_ep: Total episodes to run
    :param max_steps: Max steps per episode
    :return: DataFrame of rewards, timesteps, penalties and cost, per episode
    '''
    global OPTIMIZED
    global Q_TABLE
    if not OPTIMIZED:
        q_table, _, _, _, _ = calculate_q_table()
        Q_TABLE = q_table
        OPTIMIZED = True

    env.reset()
    total_rewards_per_ep = []
    total_penalties_per_ep = []
    total_cost_per_ep = []
    total_timesteps_per_ep = []
    print(f"TOTAL EPISODES TO BE RUN {total_test_ep}")
    last_ep = 0

    for episode in range(0, total_test_ep, 1):
        state = env.reset()

        total_rewards_in_episode = 0
        total_penalties_in_episode = 0
        total_cost_in_episode = 0
        print(f"EPISODE {episode}")
        for step in range(max_steps):

            env.render()

            # Take the action based on the Q Table:
            action = np.argmax(q_table[state, :])

            new_state, reward, done, info = env.step(action)

            total_rewards_in_episode += reward

            if reward == -10:
                total_penalties_in_episode += 1

            if total_rewards_in_episode < total_cost_in_episode:
                total_cost_in_episode = total_rewards_in_episode

            # If episode finishes:
            if done:
                total_rewards_per_ep.append(total_rewards_in_episode)
                total_timesteps_per_ep.append(step)
                total_penalties_per_ep.append(total_penalties_in_episode)
                total_cost_per_ep.append(total_cost_in_episode)
                last_ep = episode
                break

            state = new_state

        
    env.close()
    print(f"LAST EPISODE RUN: {last_ep}")
    results = pd.DataFrame({
                    'rewards': total_rewards_per_ep,
                    'timesteps':  total_timesteps_per_ep,
                    'penalties':  total_penalties_per_ep,
                    'cost':  total_cost_per_ep,
                })
    # index -> episode
    results = results.reset_index().rename(columns={'index': 'episode'})

    fig = px.bar(results, x='episode', y='timesteps')
    fig.show()
    fig = px.bar(results, x='episode', y='rewards')
    fig.show()
    fig = px.bar(results, x='episode', y='penalties')
    fig.show()
    fig = px.bar(results, x='episode', y='cost')
    fig.show()
    
    return results



## Program Backend

In [8]:
def user_mode(
    total_ep = TOTAL_EP,
    max_steps = MAX_STEPS,
    lr = LR,
    gamma = GAMMA,
    epsilon = EPSILON,
    max_epsilon = MAX_EPSILON,
    min_epsilon = MIN_EPSILON,
    decay_rate = DECAY_RATE
):
    q_table, _, _, _, _ = calculate_q_table(
        total_ep = total_ep,
        max_steps = max_steps,
        lr = lr,
        gamma = gamma,
        epsilon = epsilon,
        max_epsilon = max_epsilon,
        min_epsilon = min_epsilon,
        decay_rate = decay_rate
    )
    return  run_taxi_driver_with_calculated_q_table(total_test_ep=total_ep, q_table=q_table)

def time_mode(episodes=TOTAL_TEST_EP):
    return run_taxi_driver_with_calculated_q_table(total_test_ep=episodes)

## Program Frontend


### Time Mode
Accepts only the number of episodes desired to be run, and the optimized Q-table will be used 
#### Steps
1. Run all cells above
2. Set the amount of episodes you wish to be run
3. Run the cell and view the results

In [13]:
time_mode(
    episodes=100
)

TOTAL EPISODES TO BE RUN 100
EPISODE 0
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (West)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (West)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (West)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (Pickup)
+---------+
|R: | : :G|
|_: | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : 

episode  rewards  timesteps  penalties  cost
0         0        5         15          0   -15
1         1        5         15          0   -15
2         2        4         16          0   -16
3         3        5         15          0   -15
4         4        9         11          0   -11
..      ...      ...        ...        ...   ...
95       95        8         12          0   -12
96       96       11          9          0    -9
97       97       10         10          0   -10
98       98       10         10          0   -10
99       99        8         12          0   -12

[100 rows x 5 columns]

### User Mode
Allows the customization of the parameters to change model functionality

#### Steps
1. Run all cells above (except time mode)
2. Uncomment paramaters that you wish to change
3. Run the cell and view the results

#### Default values declared at the beginning of the notebook
MAX_STEPS = 1000
LR = 0.97
GAMMA = 0.95
EPSILON = 0.95
MAX_EPSILON = 1.0
MIN_EPSILON = 0.01
DECAY_RATE = 0.01


In [12]:
r = user_mode(
    total_ep=100,
    # max_steps=19,
#     lr=,
#     gamma=,
    epsilon=0.1,
#     max_epsilon=,
#     min_epsilon=,
#     decay_rate=0.5
)



TOTAL EPISODES TO BE RUN 100
EPISODE 0
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (West)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (Pickup)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
|_| : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
|_: : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| :_: : : |
| | : | : |
|Y| : |B: |
+---------+
  (East)
+---------+
|R: | : :G|
| : | : : |
| : :_: : |
| | : | : |
|Y| : |B: |
+---------+
  (East)
+---------+
|R: | : :G|
| : |_: 